In [ ]:
import subprocess

try:
    result = subprocess.run(['pip', 'install', 'geopy'], check=True, capture_output=True, text=True)
    print("Installation successful!")
except subprocess.CalledProcessError as e:
    # print("Error during installation:", e.stderr)
    raise e

Installation successful!


In [ ]:
ACCOUNT_KEY = dbutils.secrets.get(scope = "storage-account-secrets", key = "databricks-account-key")
ACCOUNT_NAME = dbutils.secrets.get(scope = "storage-account-secrets", key = "databricks-account-name")

In [ ]:
spark.conf.set(f"fs.azure.account.key.{ACCOUNT_NAME}.dfs.core.windows.net", ACCOUNT_KEY)

delta_table_path_final = f"abfss://swiggydataset@{ACCOUNT_NAME}.dfs.core.windows.net/main/silver/"

df_swiggy = spark.read.format("delta").load(delta_table_path_final)


In [ ]:
df_swiggy.printSchema()

root
 |-- Restaurant_ID: integer (nullable = true)
 |-- Address: string (nullable = true)
 |-- City: string (nullable = true)
 |-- Cost: double (nullable = true)
 |-- Cuisine: string (nullable = true)
 |-- Lic_No: string (nullable = true)
 |-- Rating: double (nullable = true)
 |-- Rating_count: integer (nullable = true)
 |-- Restaurant_Name: string (nullable = true)
 |-- Menu_Items: array (nullable = true)
 |    |-- element: struct (containsNull = true)
 |    |    |-- Category: string (nullable = true)
 |    |    |-- Item_Name: string (nullable = true)
 |    |    |-- Price: float (nullable = true)
 |    |    |-- Restaurant_ID: string (nullable = true)
 |    |    |-- Veg_or_Non_Veg: string (nullable = true)
 |-- Updated_Time: timestamp (nullable = true)



### Update with new data

In [ ]:
from pyspark.sql.window import Window
from pyspark.sql.functions import *

windowSpec = Window.partitionBy("Restaurant_ID").orderBy(col("Updated_Time").desc())

df_with_row_number = df_swiggy.withColumn("row_number", row_number().over(windowSpec))

df_pure = df_with_row_number.filter(col("row_number") == 1).drop("row_number")

df_pure.display()

Restaurant_ID Address City Cost Cuisine Lic_No Rating Rating_count Restaurant_Name Menu_Items Updated_Time 211 Tandoor Hut, 477, KHB Colony, 5th Block, Koramangala Koramangala,Bangalore 300.0 Biryani,Chinese 11221334000374 4.3 100 Tandoor Hut List(List(Starters, Chicken Kalmi Kebab(half), 205.0, 211, Non-veg), List(Recommended, Tandoor Chicken (half), 255.0, 211, Non-veg), List(Chinese Main Course, Chicken Fried Rice, 180.0, 211, Non-veg), List(Beverages, Coca Cola, 75.0, 211, Veg), List(Salads, Green Salad, 65.0, 211, Veg), List(Main Course, Paneer Amritsar, 230.0, 211, Veg), List(Biryani And Rice, Chicken Dum Biryani Special, 255.0, 211, Non-veg), List(Family Binge Combos, Chicken Dum Biryani + Chicken Malai Kebab(5Pcs), 405.0, 211, Non-veg), List(Indian Breads, Butter Roti, 50.0, 211, Veg), List(Soups, Cream of Veg Soup, 95.0, 211, Veg), List(Accompaniments, Roasted Papad, 35.0, 211, Veg)) 2024-12-30T07:21:25.821Z 218 Anand Sweets and Savouries, 143/A, 60 Feet Road, 5th Block, Koramangala, Bengaluru, Karnataka 560034 Koramangala,Bangalore 300.0 Sweets,Snacks 11220334000566 4.4 1000 Anand Sweets and Savouries List(List(Namkeen Packs, Rice Kodubale, 80.36, 218, Veg), List(Dry Fruits, Salted Kaju, 321.43, 218, Veg), List(Canned Sweets, Rasgulla Tin Pack, 119.1, 218, Veg), List(Fresh Malai Paneer, Paneer, 138.1, 218, Veg), List(Fresh Snacks, Veg Patties (2 Pcs), 80.0, 218, Veg), List(Gift Hampers, Silver Moon Hamper, 3428.5, 218, Veg), List(Sugarfree Range, Sugar Free Soan Papdi, 171.43, 218, Veg), List(Makhana, Makhana Sour Cream And Onion, 125.0, 218, Veg), List(Purani Dilli Main Course, Paneer Paratha PD, 150.0, 218, Veg), List(Purani Dilli Special Chaats, Raj Kachori PD, 150.0, 218, Veg), List(Teatime Bites, Yellu Murukku, 116.07, 218, Veg), List(Desserts, Raj Bhog (2 Pcs), 85.71, 218, Veg), List(Main Course, Soya Chaap & Roomali Roti, 180.0, 218, Veg), List(Beverages, Kesar Badam Milk, 90.0, 218, Veg), List(Sweets, Navratan Laddu, 233.33, 218, Veg), List(Anand Special Sharbat, Thandai, 338.98, 218, Veg), List(Festive Specials, Teej Ki Pheni, 66.67, 218, Veg), List(Gift Packs, Turkish Baklawa Square Tin, 600.0, 218, Veg), List(Chips, Gujarathi Papdi, 80.35, 218, Veg), List(Namkeens, Wafer Mixture Pack, 116.07, 218, Veg), List(Indian Bakery, Fruit Cake Rusk, 142.8, 218, Veg)) 2024-12-30T07:21:25.821Z 223 Truffles, 93/A, Appek Building, 'A' Wing, 4th 'B' Cross, Koramangala Industrial Layout, 5th Block, Koramangala, Bangalore - 560 095 Koramangala,Bangalore 450.0 American,Continental 11215334000294 4.4 5000 Truffles List(List(Pav, Mutton Kheema Pav, 247.62, 223, Non-veg), List(Burger, All American Veg Burger, 214.29, 223, Veg), List(Fries & Wedges, Classic Fries, 114.29, 223, Veg), List(Beverages, Black Currant Granita (400ML), 123.81, 223, Veg), List(Pizza, 3 Pepper & Sweet Corn Pizza [6 inch], 152.39, 223, Veg), List(Pasta, Aglio-Olio Pasta Veg, 204.77, 223, Veg), List(Truffles Special, Chocolate Lava Cake, 85.72, 223, Veg), List(Rice Bowl, Devil's Paneer Rice Bowl, 238.1, 223, Veg), List(Healthy Twist, 2 Bean & Grilled Vegetable Salad, 152.39, 223, Veg), List(Egg To Order, Fried Egg 3Pcs, 104.77, 223, Non-veg), List(Salad, Caesar Salad(Veg), 166.67, 223, Veg), List(Oriental, Fire & Spice With Rice(Veg), 276.2, 223, Veg), List(Full Cakes, Butterscotch 1/2kg, 428.58, 223, Non-veg), List(Sandwiches, Cheese S/W, 109.53, 223, Veg), List(Starters, All American Nachos Veg, 247.62, 223, Veg), List(Hot Dog, Chicken Hot Dog [Single], 133.34, 223, Non-veg), List(Add Ons, Mayo, 33.34, 223, Non-veg), List(Maincourse, Cottage Cheese Steak, 271.43, 223, Veg), List(Wraps, Mushroom & Cheese Wrap, 147.62, 223, Veg), List(Desserts, Macarons (6pcs), 285.72, 223, Non-veg), List(Submarine, Cottage Cheese Sub, 200.0, 223, Veg), List(Breakfast, Channa Masala Twist, 138.1, 223, Veg)) 2024-12-30T07:21:25.821Z 232 The Hole in the Wall Cafe, 4, 8th Main Road, 4th Block, Koramangala 4th Block, Bangalore Koramangala,Bangalore 257.0 American 112213340006

### Save as GOLD Layer

In [ ]:
spark.conf.set(f"fs.azure.account.key.{ACCOUNT_NAME}.dfs.core.windows.net",  ACCOUNT_KEY)
 
delta_table_path_final = f"abfss://swiggydataset@{ACCOUNT_NAME}.dfs.core.windows.net/main/gold/"

df_pure.write.format("delta").mode("overwrite").save(delta_table_path_final)